# OSCAR v0.11.2 Demo

Claudia Yun

[14th polymake conference and developer meeting](https://polymake.org/doku.php/workshops/workshop0223), TU Berlin, 3.2, 2023


## Install

In Julia REPL
```
using Pkg
Pkg.add("Oscar")
```

## Update
```
] update Oscar
] status Oscar
```
or
```
Pkg.add(PackageSpec(name="Oscar", version="0.11.2"))
```

In [1]:
using Pkg

In [2]:
Pkg.add(PackageSpec(name="Oscar", version="0.11.2"))

    Updating registry at `~/.julia/registries/General.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.8/Project.toml`
  No Changes to `~/.julia/environments/v1.8/Manifest.toml`


In [4]:
using Oscar

## Linear Programming

A linear program is a problem of optimizing a linear function on a polyhedron that is defined by linear inequalities.

`LinearProgram(P, c; k = 0, convention = :max)`  
P - polyhedron  
cx + k - objective function

### Joswig-Theobald Example 4.2

Maximize the linear objective function (1,1)x for x in R^2 such that x_1+5x_2 <= 20, -2x_1+x_2 <= -10, x >= 0.

We first construct the polyhedron given by the constraints. There are commonly two ways to represent a polyhedron:
- H-representation: intersection of half-spaces
- V-representation: convex hull of vertices

In this case, we use the H-representation: `Polyhedron{T}(A::AnyVecOrMat, b) where T<:scalar_types`

In [7]:
A = [1 5;-2 1;-1 0;0 -1];
b = [20,-10,0,0];
P = Polyhedron(A,b);
@show P;

P = A polyhedron in ambient dimension 2


In [9]:
c = [1,1];
l = LinearProgram(P, c; k = 0, convention = :max);
@show l;

l = The linear program
   max{c⋅x + k | x ∈ P}
where P is a Polyhedron{fmpq} and
   c=Polymake.Rational[1 1]
   k=0


In [12]:
@time max_value, vertex = solve_lp(l);

  0.000271 seconds (38 allocations: 624 bytes)


In [13]:
@show max_value;
@show vertex;

max_value = 20
vertex = fmpq[20, 0]


### View help

- Oscar documentation: [https://docs.oscar-system.org/stable/]
- ?thing, e.g.,`?LinearProgram`,`?Polyhedron`

### Exercise

A _mixed integer linear program_ is a linear program in which we require some variables to be integers.  
  
Maximize the function (2,1,1)x for x1, x3 in Z and x2 in R such that x >= 0, 2x1+5x2 <= 10 and x1-3x3 = -2. What is the maximal value? What is a point in the polyhedron that achieves that value? Is that point a vertex of the polyhedron?

## Groebner basis

Very useful tool in computational algebraic geometry. Can be used to solve ideal membership, primary decomposition, saturation, implicitization/elimination, etc.

`PolynomialRing(C::Ring, V::Vector{String}; ordering=:lex, cached = true)`

In [32]:
R, x = PolynomialRing(QQ, "x" => 1:3)

(Multivariate Polynomial Ring in x_{1}, x_{2}, x_{3} over Rational Field, fmpq_mpoly[x_{1}, x_{2}, x_{3}])

In [33]:
I = ideal(R, [x[1]*x[2], x[3]^2-x[1]^2]);

```
groebner_basis(I::MPolyIdeal;
  ordering::MonomialOrdering = default_ordering(base_ring(I)),
  complete_reduction::Bool = false, algorithm::Symbol = :buchberger)
```

In [35]:
G = groebner_basis(I, ordering = lex(R))

Gröbner basis with elements
1 -> x_{2}*x_{3}^2
2 -> x_{1}*x_{2}
3 -> x_{1}^2 - x_{3}^2
with respect to the ordering
lex([x_{1}, x_{2}, x_{3}])

## Solving integer linear programming via Groebner basis: Conti-Traverso method

### Following Joswig-Theobald Section 10.6.  

Consider the following integer linear program:  
min{cx: Ax=b, x in N^n}  

Define f_i = w_1^{a_1i}...w_m^{a_mi}, where A = (a_ij). Define I_A = (f_1-x_1,...,f_n-x_n) in the ring K\[w_1,...w_m,x_1,...,x_n\]. Let G be a Groebner basis of I_A with respect to the c-ordering. It's a bit delicate.

First order monomials in K\[x_1,...,x_n\] by declaring a \<\_c b if and only if ca < cb or (ca = cb and a < b), where < is any monomial ordering. Next extend the ordering to K\[w_1,...,w_m,x_1,...,x_n\] by declaring any monomial with a w should be larger than every monomial that consists of only the x's.  

**Proposition 10.23** implies that the ILP is feasible if and only if rem(w^b;G) is in K\[x_1,...,x_n\].

**Theorem 10.24**: If the ILP is feasible, the the remainder of w^b with respect to G, rem(w^b;G), is a monomial x^s, where s in N^n, and the multi-index s is an optimal solution.  

### Example 10.25

Consider the above ILP with A = \[2 1 1; 1 3 0\], b = \[2,3\] and c = (1,5,2). Is this ILP feasible? What is an optimal point?

In [40]:
# define rational polynomial ring with five variables
R, _ = PolynomialRing(QQ, "w"=> 1:2, "x"=> 1:3)

(Multivariate Polynomial Ring in w_{1}, w_{2}, x_{1}, x_{2}, x_{3} over Rational Field, fmpq_mpoly[w_{1}, w_{2}], fmpq_mpoly[x_{1}, x_{2}, x_{3}])

In [41]:
# rename the variables w_1, w_2, x_1 to x_3 to match the theorem
w = gens(R)[1:2]
x = gens(R)[3:5]

3-element Vector{fmpq_mpoly}:
 x_{1}
 x_{2}
 x_{3}

In [42]:
# define the generator of the ideal I_A
f1 = w[1]^2*w[2];
f2 = w[1]*w[2]^3;
f3 = w[1];

In [55]:
IA = ideal(R, [f1-x[1],f2-x[2],f3-x[3]]);

# define monomial ordering
# lex ordering on the w's; weight_ordering on the x's with lex as tie breaker
# block ordering combining the two: first compare in K[w_1,w_2,x_1,x_2,x_3]/(x_1,x_2,x_3) using lex on w, 
# then compare monomials in (x_1,x_2,x_3) by weighted degree lex.
o = lex(w)*weight_ordering([1,5,2],lex(x));

# compute Groebner basis
G = groebner_basis(IA,ordering = o);
@show G;

G = Gröbner basis with elements
1 -> x_{2}*x_{3}^5 - x_{1}^3
2 -> w_{2}*x_{1}^2 - x_{2}*x_{3}^3
3 -> w_{2}*x_{3}^2 - x_{1}
4 -> w_{2}^2*x_{1} - x_{2}*x_{3}
5 -> w_{2}^3*x_{3} - x_{2}
6 -> w_{1} - x_{3}
with respect to the ordering
lex([w_{1}, w_{2}])*matrix_ordering([x_{1}, x_{2}, x_{3}], [1 5 2])*lex([x_{1}, x_{2}, x_{3}])


In [56]:
# compute remainder of w^b after dividing by elements of the Groebner basis
reduce(w[1]^2*w[2]^3,gens(G))

x_{2}*x_{3}

What does this mean?  
x_2\*x_3 is in K\[x_1,x_2,x_3\], so this ILP is feasible. (0,1,1) is an optimal solution.

### Exercise

Contrust an Oscar MILP for this example, solve it using the native Oscar method and compare solutions.